In [1]:
words = open('names.txt', 'r').read().splitlines()

In [2]:
words[:10]

['emma',
 'olivia',
 'ava',
 'isabella',
 'sophia',
 'charlotte',
 'mia',
 'amelia',
 'harper',
 'evelyn']

In [3]:
# we want to build a trigram model.
# we will use . to indicate start and end of the words.append
chars = sorted(set(list(''.join(words))))
stoi = {s:i+1 for i,s in enumerate(chars)}
stoi['.'] = 0
itos = {i:s for s,i in stoi.items()}

In [4]:
import torch
N = torch.zeros((27,27,27), dtype=torch.int32)

In [5]:
for w in words:
    chs = ['.','.'] + list(w) + ['.']
    for chpair, ch3 in zip(zip(chs, chs[1:]), chs[2:]):
        ix1, ix2, ix3 = stoi[chpair[0]], stoi[chpair[1]], stoi[ch3]
        N[ix1, ix2, ix3] += 1



In [6]:
import matplotlib.pyplot as plt
%matplotlib inline
N_2D = N.reshape(27*27,27)
plt.figure(figsize=(512,512))
plt.imshow(N_2D, cmap='Blues')
for i in range(27):
    for j in range(27):
        for k in range(27):
            chstr = itos[i] + itos[j] + itos[k] 
            # print(chstr, N[i,j].item())
            plt.text(k, i*27+j, chstr, ha="center", va="bottom", color="gray")
            plt.text(k, i*27+j, N[i,j,k].item(), ha="center", va="top", color="gray")
plt.axis("off")

(-0.5, 26.5, 728.5, -0.5)

In [7]:
p = N[0,0] / N[0,0].sum()
p

tensor([0.0000, 0.1377, 0.0408, 0.0481, 0.0528, 0.0478, 0.0130, 0.0209, 0.0273,
        0.0184, 0.0756, 0.0925, 0.0491, 0.0792, 0.0358, 0.0123, 0.0161, 0.0029,
        0.0512, 0.0642, 0.0408, 0.0024, 0.0117, 0.0096, 0.0042, 0.0167, 0.0290])

In [11]:
N = N+1 # do only once
P = ((N) / N.sum(2, keepdim=True))
P[0,0]

tensor([3.1192e-05, 1.3759e-01, 4.0767e-02, 4.8129e-02, 5.2745e-02, 4.7785e-02,
        1.3038e-02, 2.0898e-02, 2.7293e-02, 1.8465e-02, 7.5577e-02, 9.2452e-02,
        4.9064e-02, 7.9195e-02, 3.5777e-02, 1.2321e-02, 1.6095e-02, 2.9008e-03,
        5.1154e-02, 6.4130e-02, 4.0830e-02, 2.4641e-03, 1.1759e-02, 9.6070e-03,
        4.2109e-03, 1.6719e-02, 2.9008e-02])

In [12]:
g = torch.Generator().manual_seed(402900)
ix1 = 0
ix2 = 0
for _ in range(5):
    output = ''
    while True:
        p = P[ix1, ix2]
        ix3 = torch.multinomial(p, 1, replacement=True, generator=g).item()
        output += itos[ix3]
        ix1 = ix2
        ix2 = ix3
        if ix3 == 0:
            break
    print(output)

avie.
quel.
yanottelyn.
prie.
nyerzare.


In [13]:
log_likelihood = 0.0
n = 0
for w in words:
    chs = ['.','.'] + list(w) + ['.']
    for chpair, ch3 in zip(zip(chs, chs[1:]), chs[2:]):
        ix1, ix2, ix3 = stoi[chpair[0]], stoi[chpair[1]], stoi[ch3]
        prob = P[ix1, ix2, ix3]
        log_prob = torch.log(prob)
        log_likelihood += log_prob
        n += 1
print(-log_likelihood/n)

tensor(2.2120)
